In [4]:
import os
import copy
import shutil
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mlp
%matplotlib inline
from transformers import AutoTokenizer, AutoModelWithLMHead, AutoModelForSeq2SeqLM, BartForConditionalGeneration,BartTokenizer
import shap
import scipy as sp
import nlp
import torch
pd.set_option('display.max_columns', None)
pd.set_option('max_colwidth', None)
pd.set_option("max_rows", None)
from shap.utils import assert_import, record_import_error, safe_isinstance, make_masks, OpChain, MaskedModel
from shap import maskers, links
from transformers.file_utils import ModelOutput
from shap.utils import cal_conditional_logits, GenerateLogits
import sys
np.set_printoptions(formatter={'float': lambda x: "{0:0.5f}".format(x)})

In [2]:
tokenizer = BartTokenizer.from_pretrained("sshleifer/distilbart-xsum-12-6")
model =  BartForConditionalGeneration.from_pretrained("sshleifer/distilbart-xsum-12-6").cuda()

In [3]:
dataset = nlp.load_dataset('xsum',split='train')

Using custom data configuration default


In [5]:
def gen_summary(x):
    inputs = tokenizer([x], max_length=1024, return_tensors='pt',min_length=0)
    input_ids=inputs['input_ids'].cuda()
    with torch.no_grad():
        out=model.generate(input_ids)
    decoder_inputs=out[:,:-1]
    output_names = tokenizer.convert_ids_to_tokens(out[0,1:-1])
    del out
    return {'decoder_inputs':decoder_inputs,'input_ids':input_ids,'output_names':output_names,'fixed_context':0}

In [6]:
def f_kwargs(x):
    kwargs = gen_summary(x)
    return kwargs

In [7]:
def f_cp(x_batch,**kwargs):
    output_batch=[]
    decoder_inputs=kwargs['decoder_inputs']
    for i,x in enumerate(x_batch):
        #print(f"\033[1m Masked input: \033[0m {x}")
        inputs = tokenizer([x], max_length=1024, return_tensors='pt',truncation=True)
        input_ids=inputs['input_ids']
        conditional_logits = cal_conditional_logits(model,input_ids,decoder_inputs)
        output_batch.append(conditional_logits)
    return np.array(output_batch)

In [8]:
explainer = shap.Explainer(f_cp,tokenizer,model_kwargs=f_kwargs)
explainer.masker.mask_token=None
explainer.masker.mask_token_str=""
explainer.masker.fixed_background = True

In [9]:
shap_values_1 = explainer(dataset['document'][0:1])

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Keyword arguments {'min_length': 0} not recognized.


In [11]:
shap.plots.text(shap_values_1[0])

In [12]:
logit_model = GenerateLogits(model,tokenizer)

In [37]:
def gen_summary2(x):
    inputs = tokenizer([x], max_length=1024, return_tensors='pt',min_length=0)
    input_ids=inputs['input_ids'].cuda()
    with torch.no_grad():
        out=model.generate(input_ids)
    target_sentence = [tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=False) for g in out][0]
    output_names = logit_model.get_output_names(target_sentence)
    del out
    return {'target_sentence':target_sentence,'output_names':output_names,'fixed_context':0}

In [38]:
def f_kwargs2(x):
    kwargs = gen_summary2(x)
    return kwargs

In [29]:
def f2(x_batch,**kwargs):
    output_batch=[]
    target_sentence=kwargs['target_sentence']
    for i,x in enumerate(x_batch):
        #print(f"\033[1m Masked input: \033[0m {x}")
        conditional_logits = logit_model.generate(x,target_sentence)
        output_batch.append(conditional_logits)
    return np.array(output_batch)

In [30]:
explainer2 = shap.Explainer(f2,tokenizer,model_kwargs=f_kwargs2)
explainer2.masker.mask_token=None
explainer2.masker.mask_token_str=""
explainer2.masker.fixed_background = True

In [31]:
shap_values_2 = explainer2(dataset['document'][0:1])

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Keyword arguments {'min_length': 0} not recognized.


In [26]:
shap.plots.text(shap_values_2[0])

In [32]:
shap.plots.text(shap_values_2[0])

In [39]:
def f3(x_batch,**kwargs):
    output_batch=[]
    target_sentence=kwargs['target_sentence']
    for i,x in enumerate(x_batch):
        #print(f"\033[1m Masked input: \033[0m {x}")
        inputs = tokenizer([x], max_length=1024, return_tensors='pt',min_length=0)
        input_ids=inputs['input_ids'].cuda()
        with torch.no_grad():
            out=model.generate(input_ids)
        source_sentence = [tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=False) for g in out][0]
        conditional_logits = logit_model.generate(source_sentence,target_sentence)
        output_batch.append(conditional_logits)
    return np.array(output_batch)

In [40]:
explainer3 = shap.Explainer(f3,tokenizer,model_kwargs=f_kwargs2)
explainer3.masker.mask_token=None
explainer3.masker.mask_token_str=""
explainer3.masker.fixed_background = True

In [41]:
shap_values_3 = explainer3(dataset['document'][0:1])

plicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Keyword arguments {'min_length': 0} not recognized.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Keyword arguments {'min_length': 0} not recognized.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. De

In [42]:
shap.plots.text(shap_values_3[0])